In [1]:
USE_GROQ = True  # Set to False to use OpenAI
REQUEST_DELAY = 1.5
# GROQ_MODEL = "meta-llama/llama-4-scout-17b-16e-instruct"
GROQ_MODEL = "llama3-8b-8192"
# GROQ_MODEL = "llama3-70b-8192"

In [2]:
!pip install datasets

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 491.5/491.5 kB 3.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 7.0 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 193.6/193.6 kB 8.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.5/143.5 kB 8.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.8/194.8 kB 11.2 MB/s eta 0:00:00
  Attempting uninstall: fsspec
    Found existing installation: fsspec 2025.3.2
    Uninstalling fsspec-2025.3.2:
      Successfully uninstalled fsspec-2025.3.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
torch 2.6.0+cu124 requires nvidia-cublas-cu12==12.4.5.8; platform_system == "Linux" and platform_machine == "x86_64", but you have nvidia-cublas-cu12 12.5.3.2 which is incompatible.
torch 2.6.0+cu124 requires nvidia-cuda-cupti-cu12==12.4.127; platform_system == "

In [3]:
!pip install openai
!pip install groq

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 127.5/127.5 kB 4.1 MB/s eta 0:00:00


In [4]:
# Core libraries
import os
import re
import json
from groq import Groq
import openai
import json
import ast

# Data handling
import pandas as pd
from datasets import load_dataset
from collections import defaultdict

# Evaluation (optional at this stage since you're not doing full metrics yet)
from sklearn.metrics import accuracy_score

# PyTorch (only if needed for model management or tensor ops)
import torch

from itertools import cycle
import warnings

from huggingface_hub import login
login("TOKEN")


In [5]:
# List of your GROQ API keys
GROQ_API_KEYS = [
    # paid
    "API_KEY",
]


# Create a cycling iterator over the API keys
groq_clients = [Groq(api_key=key) for key in GROQ_API_KEYS]
groq_client_cycle = cycle(groq_clients)

In [6]:
dataset_name = "cardiffnlp/databench"
semeval_train = load_dataset(dataset_name, name="qa", split="train")
# semeval_dev = load_dataset(dataset_name, name="semeval", split="dev")

# Not running:  "020_Real", "035_Billboard", "049_Boris", "054_Joe", "014_Airbnb"

train_target_datasets = [
    "001_Forbes", "002_Titanic", "004_Taxi", "005_NYC",
    "006_London", "007_Fifa", "008_Tornados", "009_Central", "010_ECommerce",
    "011_SF", "012_Heart", "013_Roller", "015_Food",
    "016_Holiday", "017_Hacker", "018_Staff", "019_Aircraft",
    "021_Telco", "022_Airbnbs", "023_Climate", "024_Salary", "025_Data",
    "026_Predicting", "027_Supermarket", "028_Predict", "029_NYTimes", "030_Professionals",
    "031_Trustpilot", "032_Delicatessen", "033_Employee", "034_World",
    "036_US", "037_Ted", "038_Stroke", "039_Happy", "040_Speed",
    "041_Airline", "042_Predict", "043_Predict", "044_IMDb", "045_Predict",
    "046_120", "047_Bank", "048_Data",  "050_ING",
    "051_Pokemon", "052_Professional", "053_Patents", "055_German",
    "056_Emoji", "057_Spain", "058_US", "059_Second", "060_Bakery",
    "061_Disneyland", "062_Trump", "063_Influencers", "064_Clustering", "065_RFM"
]

# train_target_datasets = ["060_Bakery"]
semeval_train = semeval_train.filter(lambda sample: sample['dataset'] in train_target_datasets)

/usr/local/lib/python3.11/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md:   0%|          | 0.00/43.6k [00:00<?, ?B/s]

Resolving data files:   0%|          | 0/65 [00:00<?, ?it/s]

Resolving data files:   0%|          | 0/65 [00:00<?, ?it/s]

qa.parquet:   0%|          | 0.00/7.31k [00:00<?, ?B/s]

...

qa.parquet:   0%|          | 0.00/7.03k [00:00<?, ?B/s]

qa.parquet:   0%|          | 0.00/6.40k [00:00<?, ?B/s]

qa.parquet:   0%|          | 0.00/8.08k [00:00<?, ?B/s]

Generating train split:   0%|          | 0/1308 [00:00<?, ? examples/s]

Filter:   0%|          | 0/1308 [00:00<?, ? examples/s]

In [7]:
train_dataset_map = {}
unique_train_datasets = list(set(semeval_train.unique("dataset")))

for dataset in train_target_datasets:
    train_dataset_map[dataset] = pd.read_parquet(f"hf://datasets/cardiffnlp/databench/data/{dataset}/sample.parquet")


Flattening the indices:   0%|          | 0/1185 [00:00<?, ? examples/s]

In [8]:
print(len(train_target_datasets))
print(len(train_dataset_map))

59
59


In [9]:
def clean_column_name(col_name):
    # Use regex to remove the <gx:...> part
    cleaned = re.sub(r'<gx:[^>]+>', '', col_name)
    return cleaned

for ds in train_dataset_map.keys():
    # Get the original dataframe
    df = train_dataset_map[ds]

    column_mapping = {col: clean_column_name(col) for col in df.columns}

    # Rename the columns in the dataframe
    df = df.rename(columns=column_mapping)

    # Store the updated dataframe back in the hashmap
    train_dataset_map[ds] = df

In [10]:
def safe_parse_list(raw):
    import ast
    import re

    if isinstance(raw, list):
        return raw

    if isinstance(raw, str):
        try:
            # Step 1: Try literal_eval first (may work if quotes are fine)
            parsed = ast.literal_eval(raw)
            if isinstance(parsed, list):
                return parsed
        except:
            pass

        try:
            # Step 2: Manually repair unquoted or single-quoted elements
            if raw.startswith("[") and raw.endswith("]"):
                inner = raw[1:-1].strip()
                if inner and not inner.startswith(("'", '"')):
                    # Case: [Weight, Height]
                    parts = [p.strip() for p in inner.split(",")]
                    quoted = [f'"{p}"' for p in parts if p]
                    fixed = "[" + ", ".join(quoted) + "]"
                else:
                    # Case: ["What's your name?"]
                    # Escape inner quotes
                    inner = raw[1:-1]
                    fixed_inner = re.sub(r'(["\'])', r'\\\1', inner)
                    fixed = f'["{fixed_inner}"]'
                parsed = ast.literal_eval(fixed)
                if isinstance(parsed, list):
                    return parsed
        except Exception as e:
            print(f"Failed to parse used_cols string: {raw} | Reason: {e}")

    return raw # should never happen

def clean_columns_used(col_list):
    parsed = safe_parse_list(col_list)

    if not isinstance(parsed, list):
        return [str(parsed)] if parsed is not None else []

    cleaned = []
    for col in parsed:
        col = str(col)
        col = re.sub(r"<gx:[^>]+>", "", col).strip()
        cleaned.append(col)
    return cleaned

def update_columns_used(example):
    example["columns_used"] = clean_columns_used(example.get("columns_used"))
    return example



semeval_train = semeval_train.map(update_columns_used)

Map:   0%|          | 0/1185 [00:00<?, ? examples/s]

In [11]:
def serialize_to_kv_format(df, dropna=True):
    kv_serialized = []
    for _, row in df.iterrows():
        kv_pairs = []
        for col, val in row.items():
            if pd.isna(val) and dropna:
                continue
            if isinstance(val, str):
                val = f'"{val}"'
            kv_pairs.append(f"{col}: {val}")
        row_str = "{" + ", ".join(kv_pairs) + "}"
        kv_serialized.append(row_str)
    return kv_serialized

In [12]:
def try_parse_list(val):
    """Try to parse a stringified list, else return original"""
    if isinstance(val, str) and val.startswith("[") and val.endswith("]"):
        try:
            parsed = ast.literal_eval(val)
            if isinstance(parsed, list):
                return parsed
        except:
            pass
    return val

def detect_url(val) -> bool:
    if not isinstance(val, str):
        return False
    val = val.strip()
    return val.startswith("http://") or val.startswith("https://") or val.startswith("www.")

def detect_number(val) -> bool:
    try:
        return isinstance(val, (int, float)) or float(str(val))
    except:
        return False

def detect_boolean(val) -> bool:
    if isinstance(val, bool): return True
    if isinstance(val, str): return val.strip().lower() in ["true", "false"]
    if isinstance(val, (int, float)): return val in [0, 1]
    return False

def detect_date(val) -> bool:
    try:
        # Suppress UserWarning about ambiguous day/month formats
        with warnings.catch_warnings():
            warnings.simplefilter("ignore", UserWarning)
            parsed = pd.to_datetime(val, errors="raise", dayfirst=False)
        return isinstance(parsed, pd.Timestamp)
    except Exception:
        try:
            with warnings.catch_warnings():
                warnings.simplefilter("ignore", UserWarning)
                parsed = pd.to_datetime(val, errors="raise", dayfirst=True)
            return isinstance(parsed, pd.Timestamp)
        except:
            return False

def get_column_type(values, col_name="", sample_size=20) -> str:
    # Parse stringified lists
    parsed = [try_parse_list(v) for v in values if pd.notna(v) and v not in ["", "nan", "NaN"]]
    parsed = parsed[:sample_size]

    if not parsed:
        if "category" in col_name.lower() or "id" in col_name.lower():
            return "category"
        return "empty"

    first = parsed[0]

    # List-type
    if isinstance(first, list):
        inner_vals = [item for sublist in parsed if isinstance(sublist, list) for item in sublist]
        if not inner_vals:
            return "list[empty]"
        if all(detect_number(v) for v in inner_vals):
            return "list[number]"
        if all(detect_url(v) for v in inner_vals):
            return "list[url]"
        if all(detect_boolean(v) for v in inner_vals):
            return "list[boolean]"
        return "list[category]"

    # Scalar-type
    if all(detect_boolean(v) for v in parsed): return "boolean"
    if all(detect_number(v) for v in parsed): return "number"
    if all(detect_url(v) for v in parsed): return "url"
    if all(detect_date(v) for v in parsed): return "date"
    if len(set(map(str, parsed))) < sample_size / 2: return "category"
    if any(len(str(v)) > 30 for v in parsed): return "text"
    return "string"

def get_column_info(df: pd.DataFrame, sample_size: int = 20) -> dict:
    """
    Infers rich, normalized column types based on sample values,
    including nested and stringified list types.

    Returns:
        dict mapping column name -> inferred type label (e.g., list[category], boolean, date, etc.)
    """
    return {
        col: get_column_type(df[col].tolist(), col_name=col, sample_size=sample_size)
        for col in df.columns
    }


In [13]:
def build_phase1_prompt(question: str, column_info: dict) -> str:
    """
    Constructs a prompt for Phase 1 of the column-selection QA pipeline.

    This function formats a prompt to be used with a large language model to identify
    the most relevant columns for answering a given question. The column metadata is
    passed as a dictionary of {column_name: column_type}, and the model is instructed
    to return a Python list of column names.

    Parameters:
    ----------
    question : str
        The natural language question for which relevant columns should be selected.
    column_info : dict
        A dictionary mapping column names (str) to their data types (str), e.g.,
        {"Country": "string", "GDP_2020": "float", ...}

    Returns:
    -------
    str
        A prompt string asking the LLM to return a Python list of column names
        most relevant to answering the question. The question is enclosed between
        <question> and </question> delimiters for clarity.
    """
    columns_as_dict_str = "{\n" + ",\n".join(
        f'  "{col}": "{dtype}"' for col, dtype in column_info.items()
    ) + "\n}"

    prompt = (
        "You are given a natural language question and a dictionary of table columns with their data types.\n"
        "Your task is to select the names of the columns that are most relevant for answering the question.\n"
        "Select only the minimal set of columns needed to answer the question accurately.\n"
        "Return the result as a Python list of strings. Do not include any explanation.\n"
        "The question is delimited by <question> and </question>.\n\n"
        f"<question>\n{question}\n</question>\n\n"
        f"Columns:\n{columns_as_dict_str}"
    )

    return prompt


In [14]:
def build_phase2_prompt(df: pd.DataFrame, question: str) -> str:
    """
    Constructs a prompt for Phase 2 of the column-selection QA pipeline.

    This function formats a prompt for a large language model to generate an answer
    based on a filtered DataFrame containing only the columns selected in Phase 1.
    The table is serialized into a key-value format, and the model is asked to return
    a JSON object containing only the final answer using Python-native types.

    Parameters:
    ----------
    df : pd.DataFrame
        A DataFrame containing only the relevant columns and rows needed to answer the question.
    question : str
        The natural language question to be answered using the filtered table data.

    Returns:
    -------
    str
        A prompt string formatted for an instruction-tuned LLM, using a [INST]...[/INST] block.
        The model is expected to return a JSON object with a single key: "answer".
    """
    kv_serialized = serialize_to_kv_format(df)

    response_format = (
        'You must answer in a single JSON with one field:\n'
        '* "answer": your final answer based on the records.'
    )

    prompt_body = (
        "You are an assistant tasked with answering questions asked of a given dataset in JSON format.\n"
        f"{response_format}\n"
        "Requirements:\n"
        "* Only respond with the JSON. Do not include explanations or full objects.\n"
        "* Your answer must use valid Python data types:\n"
        "  - Use `True` or `False` (capitalized) for boolean values.\n"
        "  - Use numbers as Python `int` or `float` (e.g., `3`, `3.14`).\n"
        "  - Use double-quoted Python strings for categorical values (e.g., \"USA\").\n"
        "  - Use Python lists for answers involving multiple values:\n"
        "    - For list[category], return a list of strings.\n"
        "    - For list[number], return a list of ints or floats.\n"
        "    - Ensure all inner values match the correct type.\n\n"
        "In the following key-value formatted data:\n"
        "```kv\n"
        f"{kv_serialized}\n"
        "```\n"
        f"USER: {question}\n"
        "ASSISTANT:"
    )

    return f"[INST]\n{prompt_body}\n[/INST]"


In [15]:
def generate_model_response(prompt):
    """
    Generates a response using Groq (LLaMA-3) or OpenAI (GPT-3.5).
    Falls back across multiple Groq keys if needed.
    """
    if USE_GROQ:
        for attempt in range(len(groq_clients)):
            groq_client = next(groq_client_cycle)

            try:
                response = groq_client.chat.completions.create(
                    model=GROQ_MODEL,
                    messages=[{"role": "user", "content": prompt}],
                    temperature=0.7,
                    max_tokens=512,
                    top_p=1.0
                )
                return response.choices[0].message.content

            except Exception as e:
                print(f"[Groq Attempt {attempt + 1}] Error: {e}")
                continue

        return "All Groq API keys exhausted or rate limited."

    else:
        try:
            response = openai.ChatCompletion.create(
                model="gpt-3.5-turbo",
                messages=[{"role": "user", "content": prompt}],
                temperature=0.7,
                max_tokens=512,
                top_p=1.0
            )
            return response.choices[0].message["content"]

        except Exception as e:
            return f"OpenAI request failed: {e}"


In [17]:
def normalize_number(value):
    if isinstance(value, (int, float)):
        return float(value)
    if isinstance(value, str):
        return float(value.strip())
    raise ValueError(f"Expected numeric type for number, got: {type(value)}")

def normalize_category(value):
    if isinstance(value, str):
        return value.strip()
    raise ValueError(f"Expected string for category, got: {type(value)}")

def normalize_boolean(value):
    if isinstance(value, bool):
        return value
    if isinstance(value, str):
        val = value.strip().lower()
        if val in {"true", "1", "yes"}:
            return True
        elif val in {"false", "0", "no"}:
            return False
        else:
            raise ValueError(f"Unrecognized string for boolean: {value!r}")
    if isinstance(value, (int, float)):
        if value == 1:
            return True
        elif value == 0:
            return False
        else:
            raise ValueError(f"Numeric value not valid for boolean: {value}")
    raise ValueError(f"Expected bool, int, float, or string for boolean, got: {type(value)}")



In [18]:
def normalize_list_category(answer):
    """
    Normalize an answer of type list[category] into a set of cleaned strings.
    Handles both true lists and stringified list representations,
    and removes stray square brackets from individual elements.
    """
    def clean_item(x):
        x = str(x).strip()
        if x.startswith("["):
            x = x[1:]
        if x.endswith("]"):
            x = x[:-1]
        return x.strip()
    if isinstance(answer, str):
        try:
            parsed = ast.literal_eval(answer)
            if isinstance(parsed, list):
                answer = parsed
            else:
                answer = [item.strip() for item in answer.split(",") if item.strip()]
        except:
            answer = [item.strip() for item in answer.split(",") if item.strip()]
    if isinstance(answer, list):
        return set(clean_item(x) for x in answer)
    return set()  # fallback


In [19]:
def normalize_list_number(value):
    """
    Normalizes a predicted or gold value for list[number] questions.

    Expected input:
    - a string representing a list of numbers, e.g., "[2, 2, 2]"
    - OR a Python list of numbers
    - OR a stringified CSV like "2, 2, 2"

    Returns:
    - A set of floats
    """
    try:
        if isinstance(value, str):
            try:
                # Try parsing as JSON list
                value = json.loads(value)
            except json.JSONDecodeError:
                try:
                    value = ast.literal_eval(value)
                except:
                    # fallback: comma-separated
                    value = [item.strip() for item in value.split(",") if item.strip()]
        return set(float(v) for v in value)
    except Exception as e:
        print(f"normalize_list_number error: {e}")
        return None


In [20]:
def normalize_answer(value, expected_type):
    """
    Dispatches to the appropriate normalization function based on expected_type.
    """
    try:
        if expected_type == "number":
            return normalize_number(value)
        elif expected_type == "category":
            return normalize_category(value)
        elif expected_type == "boolean":
            return normalize_boolean(value)
        elif expected_type == "list[category]":
            return normalize_list_category(value)
        elif expected_type == "list[number]":
            return normalize_list_number(value)
        else:
            raise ValueError(f"Unsupported expected type: {expected_type}")
    except Exception as e:
        print(f"normalize_answer error for type '{expected_type}': {e}")
        return None


In [21]:
def normalize_columns(value):
    """
    Normalize a gold or predicted column list into a set of strings,
    preserving casing and special characters.
    """
    try:
        if isinstance(value, str):
            # Try parsing as a list
            try:
                parsed = ast.literal_eval(value)
                if isinstance(parsed, list):
                    value = parsed
                else:
                    # fallback: comma-split string
                    value = [item.strip() for item in value.split(",") if item.strip()]
            except:
                value = [item.strip() for item in value.split(",") if item.strip()]

        if isinstance(value, list):
            return set(str(x).strip() for x in value)

    except Exception as e:
        print(f"normalize_columns error: {e}")

    return set()  # fallback


In [22]:
import json
import ast

def process_response(generated_text, question, expected_type, error_set):
    """
    Processes the raw LLM response to extract and normalize the answer and columns.

    Args:
        generated_text (str): Raw text output from the LLM.
        question (str): The question (used for debugging).
        expected_type (str): The expected type of the answer (e.g., boolean, number).
        error_set (set): A set to store questions that had format errors.

    Returns:
        Tuple[bool, Any, List[str]]:
            - is_error (bool): True if formatting/parsing failed.
            - norm_answer: normalized answer or None on failure.
            - norm_columns: normalized list of columns or [] on failure.
    """
    is_error = False
    norm_answer = None
    norm_columns = []

    try:
        # Step 1: Trim response
        generated_text = generated_text.strip()

        # Step 2: Try to isolate a dictionary from the output
        start = generated_text.find('{')
        end = generated_text.rfind('}') + 1
        if start == -1 or end == -1:
            raise ValueError("Could not find a JSON-like object")

        json_str = generated_text[start:end]

        # Fix lowercase true/false if needed
        json_str_fixed = json_str.replace("true", "True").replace("false", "False")

        # Step 3: Try parsing as JSON first, fallback to ast.literal_eval
        try:
            response_json = json.loads(json_str)
        except json.JSONDecodeError:
            response_json = ast.literal_eval(json_str_fixed)

        # Step 4: Ensure expected keys exist
        if "answer" not in response_json:
            raise KeyError("Missing 'answer' or 'columns_used' in response")

        raw_answer = response_json["answer"]
        # raw_columns = response_json["columns_used"]

        # Step 5: Normalize both fields
        norm_answer = normalize_answer(raw_answer, expected_type)
        # norm_columns = normalize_columns(raw_columns)

    except Exception as e:
        # On any failure, flag error and return safe defaults
        print(f"[process_response] Failed to parse response for question: {question}")
        print(f"Error: {e}")
        is_error = True
        error_set.add(question)
        norm_answer = None
        norm_columns = []

    # Return tuple: (was error?, normalized answer, normalized columns)
    return is_error, norm_answer, norm_columns


In [23]:
# STEP 1: Extract metadata from the dev set
example = semeval_train[0]
question = example["question"]
dataset_id = example["dataset"]
expected_type = example["type"]
true_answer = normalize_answer(example["sample_answer"], expected_type)
true_columns = normalize_columns(example["columns_used"])

print(f"Type(true_answer) {type(true_answer)}")
print(f"Type(true_columns) {type(true_columns)}")

# STEP 2: Load the table
df = train_dataset_map[dataset_id]

# STEP 3: Run Phase 1 — Column Selection
column_info = get_column_info(df)
phase1_prompt = build_phase1_prompt(question, column_info)
print("\n=== Phase 1 Prompt ===")
print(phase1_prompt[:1000])

raw_col_response = generate_model_response(phase1_prompt)
print("\n=== Phase 1 Raw LLM Output ===")
print(raw_col_response)

try:
    selected_columns = ast.literal_eval(raw_col_response.strip())
    print(f"\nSelected Columns (Phase 1): {selected_columns}")
    filtered_df = df[selected_columns]
except Exception as e:
    print(f"Failed to parse selected columns: {e}")
    selected_columns = []
    filtered_df = df  # fallback to full table

# STEP 4: Run Phase 2 — Answer Generation
phase2_prompt = build_phase2_prompt(filtered_df, question)
print("\n=== Phase 2 Prompt ===")
print(phase2_prompt[:1000])

raw_answer_response = generate_model_response(phase2_prompt)
print("\n=== Phase 2 Raw LLM Output ===")
print(raw_answer_response)

# STEP 5: Postprocess answer
sample_error_set = set()
is_error, pred_answer, _ = process_response(raw_answer_response, question, expected_type, sample_error_set)
pred_cols = set(selected_columns)

# STEP 6: Print results
print(f"\nType(pred_answer) {type(pred_answer)}")
print(f"Type(pred_columns) {type(pred_cols)}")

print(f"\nQuestion: {question}")
print(f"Is Error? : {is_error}")
print(f"Gold Columns: {true_columns}, Predicted: {pred_cols}\n")
print(f"Gold Answer: {true_answer}, Predicted: {pred_answer}")


Type(true_answer) <class 'bool'>
Type(true_columns) <class 'set'>

=== Phase 1 Prompt ===
You are given a natural language question and a dictionary of table columns with their data types.
Your task is to select the names of the columns that are most relevant for answering the question.
Select only the minimal set of columns needed to answer the question accurately.
Return the result as a Python list of strings. Do not include any explanation.
The question is delimited by <question> and </question>.

<question>
Is the person with the highest net worth self-made?
</question>

Columns:
{
  "selfMade": "boolean",
  "finalWorth": "number",
  "city": "string",
  "title": "category",
  "gender": "category",
  "age": "number",
  "rank": "number",
  "philanthropyScore": "number",
  "category": "category",
  "source": "string",
  "country": "string"
}

=== Phase 1 Raw LLM Output ===
['finalWorth', 'selfMade']

Selected Columns (Phase 1): ['finalWorth', 'selfMade']

=== Phase 2 Prompt ===
[INST]

In [24]:
import time

def safe_generate_response(prompt, retries=1, delay=3):
    attempts = 0
    while attempts <= retries:
        try:
            return generate_model_response(prompt)
        except Exception as e:
            print(f"[Attempt {attempts+1}] Error: {repr(e)}")
            time.sleep(delay)
            attempts += 1
    print("Failed all attempts. Returning empty response.")
    return ""


In [25]:
def evaluate_dataset(dataset_rows, dataset_name, dev_dataset_map, request_delay=1.5):
    pred_answers = []
    gold_answers = []
    pred_columns = []
    gold_columns = []
    question_types = []

    type_wise_correct = defaultdict(int)
    type_wise_total = defaultdict(int)
    column_match_count = 0
    error_set = set()
    formatting_errors_by_type = defaultdict(int)

    print(f"# Questions in {dataset_name}: {len(dataset_rows)}")

    for i, row in enumerate(dataset_rows):
        print(f"\n--- Query {i+1}/{len(dataset_rows)} ---")

        question = row["question"]
        dataset = row["dataset"]
        expected_type = row["type"]

        gold_answer = normalize_answer(row["sample_answer"], expected_type)
        gold_cols = normalize_columns(row["columns_used"])

        # --- Load full table ---
        full_df = dev_dataset_map[dataset]

        # --- Phase 1: Column Selection ---
        column_info = get_column_info(full_df)
        phase1_prompt = build_phase1_prompt(question, column_info)
        print("\n=== Phase 1 Prompt ===")
        print(phase1_prompt[:1000])
        raw_col_response = generate_model_response(phase1_prompt)
        print("\n=== Phase 1 Raw LLM Output ===")
        print(raw_col_response)

        try:
            selected_columns = ast.literal_eval(raw_col_response.strip())
            filtered_df = full_df[selected_columns]
        except Exception as e:
            print(f"[Phase 1 Error] Failed to parse selected columns: {e}")
            selected_columns = []
            filtered_df = full_df  # fallback to full table

        pred_cols = set(selected_columns)

        # --- Phase 2: Answer Generation ---
        phase2_prompt = build_phase2_prompt(filtered_df, question)
        print("\n=== Phase 2 Prompt ===")
        print(phase2_prompt[:1000])
        raw_answer_response = generate_model_response(phase2_prompt)
        print("\n=== Phase 2 Raw LLM Output ===")
        print(raw_answer_response)
        time.sleep(request_delay)

        # --- Parse Answer Only ---
        is_error, pred_answer, _ = process_response(raw_answer_response, question, expected_type, error_set)
        if is_error:
            formatting_errors_by_type[expected_type] += 1

        print(f"\nQuestion: {question}")
        print(f"Pred Answer: {pred_answer}, Gold Answer: {gold_answer}")
        print(f"Pred Columns: {pred_cols}, Gold Columns: {gold_cols}")

        # --- Append Results ---
        pred_answers.append(pred_answer)
        gold_answers.append(gold_answer)
        pred_columns.append(pred_cols)
        gold_columns.append(gold_cols)
        question_types.append(expected_type)
        type_wise_total[expected_type] += 1

        # --- Answer Accuracy ---
        correct = False
        try:
            if expected_type == "number":
                correct = abs(pred_answer - gold_answer) < 1e-3
            else:
                correct = pred_answer == gold_answer
        except:
            correct = False

        if correct:
            type_wise_correct[expected_type] += 1

        # --- Column Accuracy ---
        if isinstance(pred_cols, (list, set)) and set(pred_cols) == set(gold_cols):
            column_match_count += 1

    print("\n=== Answer Accuracy by Type ===")
    for qtype in type_wise_total:
        total = type_wise_total[qtype]
        correct = type_wise_correct[qtype]
        acc = correct / total if total else 0
        print(f"{qtype:15}: {acc:.2%} ({correct}/{total})")

    total = len(dataset_rows)
    col_acc = column_match_count / total if total else 0
    print(f"\n=== Column Selection Accuracy ===\n{col_acc:.2%} ({column_match_count}/{total})")

    eval_records = []
    for i in range(len(dataset_rows)):
        eval_records.append({
            "type": question_types[i],
            "gold_answer": gold_answers[i],
            "pred_answer": pred_answers[i],
            "gold_columns": gold_columns[i],
            "pred_columns": pred_columns[i],
        })

    # --- Final Column Stats ---
    wrong_cols = 0
    right_cols = 0
    format_errors = 0
    for i, (pred, gold) in enumerate(zip(pred_columns, gold_columns)):
        question = dataset_rows[i]["question"]

        if question in error_set:
            format_errors += 1
            continue

        if isinstance(pred, (list, set)):
            if set(pred) == set(gold):
                right_cols += 1
            else:
                wrong_cols += 1
        else:
            format_errors += 1  # fallback

    column_stats = {
        "wrong_cols": wrong_cols,
        "right_cols": right_cols,
        "format_error": format_errors,
        "total": len(dataset_rows)
    }

    return eval_records, column_stats, formatting_errors_by_type


In [26]:
def compute_metrics(eval_records, model_name, model_results):
    results = defaultdict(float)
    total = len(eval_records)
    correct_all = 0
    typewise = defaultdict(lambda: [0, 0])
    colwise = {'single': [0, 0], 'multi': [0, 0]}

    for record in eval_records:
        t = record['type']
        gold_answer = record['gold_answer']
        pred_answer = record['pred_answer']
        gold_cols = set(record['gold_columns'])
        pred_cols = set(record['pred_columns'])

        try:
            if t == "number":
                answer_match = abs(pred_answer - gold_answer) < 1e-3
            else:
                answer_match = pred_answer == gold_answer
        except:
            answer_match = False

        col_match = gold_cols == pred_cols
        joint_match = answer_match and col_match
        if joint_match:
            correct_all += 1

        typewise[t][1] += 1
        if joint_match:
            typewise[t][0] += 1

        col_count = len(gold_cols)
        if col_count == 1:
            colwise['single'][1] += 1
            if joint_match:
                colwise['single'][0] += 1
        else:
            colwise['multi'][1] += 1
            if joint_match:
                colwise['multi'][0] += 1

    def get_acc(dic, key):
        correct, total = dic[key]
        return correct / total if total else 0

    results['avg'] = correct_all / total if total else 0
    results['boolean'] = get_acc(typewise, 'boolean')
    results['number'] = get_acc(typewise, 'number')
    results['category'] = get_acc(typewise, 'category')
    results['list[category]'] = get_acc(typewise, 'list[category]')
    results['list[number]'] = get_acc(typewise, 'list[number]')
    results['single col'] = get_acc(colwise, 'single')
    results['multiple cols'] = get_acc(colwise, 'multi')

    model_results[model_name] = dict(results)


In [27]:
def format_percent_and_count(val, total):
    percent = 100 * val / total if total else 0
    return f"{percent:.1f} ({val})"

In [28]:
all_eval_records = []
model_results = {}
column_quality_table = []
formatting_errors_summary = defaultdict(int)

for dataset_id in train_target_datasets:

    dataset_rows = semeval_train.filter(lambda sample: sample["dataset"] == dataset_id)
    print(f"\n\n### Evaluating {dataset_id} ###")

    records, col_stats, formatting_errors_by_type = evaluate_dataset(
        dataset_rows, dataset_name=dataset_id, dev_dataset_map=train_dataset_map
    )

    compute_metrics(records, dataset_id, model_results)

    all_eval_records.extend(records)

    column_quality_table.append({
        "model": dataset_id,
        "wrong cols": format_percent_and_count(col_stats["wrong_cols"], col_stats["total"]),
        "right cols": format_percent_and_count(col_stats["right_cols"], col_stats["total"]),
        "format error": format_percent_and_count(col_stats["format_error"], col_stats["total"]),
    })

    for qtype, count in formatting_errors_by_type.items():
        formatting_errors_summary[qtype] += count

Filter:   0%|          | 0/1185 [00:00<?, ? examples/s]



### Evaluating 001_Forbes ###
# Questions in 001_Forbes: 25

--- Query 1/25 ---

=== Phase 1 Prompt ===
You are given a natural language question and a dictionary of table columns with their data types.
Your task is to select the names of the columns that are most relevant for answering the question.
Select only the minimal set of columns needed to answer the question accurately.
Return the result as a Python list of strings. Do not include any explanation.
The question is delimited by <question> and </question>.

<question>
Is the person with the highest net worth self-made?
</question>

Columns:
{
  "selfMade": "boolean",
  "finalWorth": "number",
  "city": "string",
  "title": "category",
  "gender": "category",
  "age": "number",
  "rank": "number",
  "philanthropyScore": "number",
  "category": "category",
  "source": "string",
  "country": "string"
}

=== Phase 1 Raw LLM Output ===
['selfMade', 'finalWorth']

=== Phase 2 Prompt ===
[INST]
You are an assistant tasked with answer

Filter:   0%|          | 0/1185 [00:00<?, ? examples/s]



### Evaluating 002_Titanic ###
# Questions in 002_Titanic: 20

--- Query 1/20 ---

=== Phase 1 Prompt ===
You are given a natural language question and a dictionary of table columns with their data types.
Your task is to select the names of the columns that are most relevant for answering the question.
Select only the minimal set of columns needed to answer the question accurately.
Return the result as a Python list of strings. Do not include any explanation.
The question is delimited by <question> and </question>.

<question>
Did any children below the age of 18 survive?
</question>

Columns:
{
  "Age": "number",
  "Siblings_Spouses Aboard": "number",
  "Sex": "category",
  "Name": "text",
  "Pclass": "number",
  "Fare": "number",
  "Survived": "boolean"
}

=== Phase 1 Raw LLM Output ===
['Age', 'Survived']

=== Phase 2 Prompt ===
[INST]
You are an assistant tasked with answering questions asked of a given dataset in JSON format.
You must answer in a single JSON with one field:
* "a

Filter:   0%|          | 0/1185 [00:00<?, ? examples/s]

...



### Evaluating 063_Influencers ###
# Questions in 063_Influencers: 20

--- Query 1/20 ---

=== Phase 1 Prompt ===
You are given a natural language question and a dictionary of table columns with their data types.
Your task is to select the names of the columns that are most relevant for answering the question.
Select only the minimal set of columns needed to answer the question accurately.
Return the result as a Python list of strings. Do not include any explanation.
The question is delimited by <question> and </question>.

<question>
Are there any organizations in the dataset?
</question>

Columns:
{
  "name": "string",
  "weight": "number",
  "x": "number",
  "is_organization": "boolean",
  "community": "number",
  "id": "number",
  "page_rank_norm": "number",
  "y": "number",
  "pic": "url"
}

=== Phase 1 Raw LLM Output ===
['name', 'is_organization']

=== Phase 2 Prompt ===
[INST]
You are an assistant tasked with answering questions asked of a given dataset in JSON format.
You mu

Filter:   0%|          | 0/1185 [00:00<?, ? examples/s]



### Evaluating 064_Clustering ###
# Questions in 064_Clustering: 20

--- Query 1/20 ---

=== Phase 1 Prompt ===
You are given a natural language question and a dictionary of table columns with their data types.
Your task is to select the names of the columns that are most relevant for answering the question.
Select only the minimal set of columns needed to answer the question accurately.
Return the result as a Python list of strings. Do not include any explanation.
The question is delimited by <question> and </question>.

<question>
Are there any animals with feathers in the dataset?
</question>

Columns:
{
  "legs": "number",
  "domestic": "boolean",
  "breathes": "boolean",
  "class_type": "number",
  "venomous": "boolean",
  "feathers": "boolean",
  "animal_name": "string"
}

=== Phase 1 Raw LLM Output ===
['class_type', 'feathers']

=== Phase 2 Prompt ===
[INST]
You are an assistant tasked with answering questions asked of a given dataset in JSON format.
You must answer in a sing

Filter:   0%|          | 0/1185 [00:00<?, ? examples/s]



### Evaluating 065_RFM ###
# Questions in 065_RFM: 20

--- Query 1/20 ---

=== Phase 1 Prompt ===
You are given a natural language question and a dictionary of table columns with their data types.
Your task is to select the names of the columns that are most relevant for answering the question.
Select only the minimal set of columns needed to answer the question accurately.
Return the result as a Python list of strings. Do not include any explanation.
The question is delimited by <question> and </question>.

<question>
Are all the quantities greater than 0?
</question>

Columns:
{
  "InvoiceNo": "string",
  "Country": "category",
  "StockCode": "string",
  "Description": "text",
  "Quantity": "number",
  "CustomerID": "number",
  "UnitPrice": "number"
}

=== Phase 1 Raw LLM Output ===
["Quantity", "UnitPrice"]

=== Phase 2 Prompt ===
[INST]
You are an assistant tasked with answering questions asked of a given dataset in JSON format.
You must answer in a single JSON with one field:
* 

In [32]:
# Table 1: Main Metrics Table (per dataset)
results_df = pd.DataFrame(model_results).T.round(3)
print("### Main Metrics Table:")
print(results_df.to_markdown())

# Table 2: Column Quality Table (per dataset)
col_df = pd.DataFrame(column_quality_table)
print("\n### Column Quality Table:")
print(col_df.to_markdown(index=False))

# Table 3: Formatting Errors by Question Type
print("\n### Formatting Errors by Question Type:")
for qtype, count in formatting_errors_summary.items():
    print(f"{qtype:15}: {count} formatting errors")

### Main Metrics Table:
|                   |   avg |   boolean |   number |   category |   list[category] |   list[number] |   single col |   multiple cols |
|:------------------|------:|----------:|---------:|-----------:|-----------------:|---------------:|-------------:|----------------:|
| 001_Forbes        |  0.2  |      0    |     0.2  |       0.6  |             0    |           0.2  |        0     |           0.278 |
| 002_Titanic       |  0.2  |      0    |     0.5  |       0.25 |             0    |           0.25 |        0.286 |           0.154 |
| 004_Taxi          |  0    |      0    |     0    |       0    |             0    |           0    |        0     |           0     |
| 005_NYC           |  0.05 |      0    |     0    |       0    |             0    |           0.25 |        0.05  |           0     |
| 006_London        |  0.2  |      0.5  |     0.25 |       0    |             0    |           0.25 |        0.2   |           0     |
| 007_Fifa          |  0.2  |  

In [33]:
# Store dataset sizes
dataset_sizes = {dataset_id: len(semeval_train.filter(lambda s: s["dataset"] == dataset_id)) for dataset_id in train_target_datasets}

def compute_weighted_global_metrics(model_results, dataset_sizes):
    weighted_sums = defaultdict(float)
    total_size = sum(dataset_sizes[ds] for ds in model_results if ds != "GLOBAL")

    for dataset_id, metrics in model_results.items():
        if dataset_id == "GLOBAL":
            continue
        weight = dataset_sizes[dataset_id]
        for k, v in metrics.items():
            weighted_sums[k] += v * weight

    return {k: weighted_sums[k] / total_size for k in weighted_sums}

# Compute and store weighted global average
global_model_results = {}
global_model_results["GLOBAL"] = compute_weighted_global_metrics(model_results, dataset_sizes)

# Display as markdown table
global_df = pd.DataFrame(global_model_results).T.round(3)
print("\n### Global Metrics Across All Datasets (Weighted):")
print(global_df.to_markdown())


### Global Metrics Across All Datasets (Weighted):
|        |   avg |   boolean |   number |   category |   list[category] |   list[number] |   single col |   multiple cols |
|:-------|------:|----------:|---------:|-----------:|-----------------:|---------------:|-------------:|----------------:|
| GLOBAL | 0.184 |     0.207 |    0.215 |      0.265 |            0.118 |          0.114 |          0.2 |           0.175 |
